![image.png](https://images.aicrowd.com/raw_images/challenges/banner_file/1007/6edbed5d4a9dd4d28f16.jpg)

<h2><center>Starter Code for NLP Feature Engineering #2</center></h2>

<!-- <h6><center>Author : Shubhamai</center></h6> -->



<!-- --- -->



### What we are going to Learn

  - How to convert your text into numbers ?
  - How Bag of words, TF-IDF works ?
  - Testing and Submitting the Results to the Challenge. 

## About this Challanges

Now, this challange is very different form what we usually do in AIcrowd Blitz.In this challanges, the task is to generate features from a text data. Extracting features helps up to generate text embeddings will contains more useful information about the text. 


# Setup AIcrowd Utilities 🛠

We use this to bundle the files for submission and create a submission on AIcrowd. Do not edit this block.

In [62]:
!pip install -q -U aicrowd-cli
%load_ext aicrowd.magic

The aicrowd.magic extension is already loaded. To reload it, use:
  %reload_ext aicrowd.magic


## How to use this notebook? 📝

<p style="text-align: center"><img src="https://gitlab.aicrowd.com/aicrowd/assets/-/raw/master/notebook/aicrowd_notebook_submission_flow.png?inline=false" alt="notebook overview" style="width: 650px;"/></p>

- **Update the config parameters**. You can define the common variables here

Variable | Description
--- | ---
`AICROWD_DATASET_PATH` | Path to the file containing test data (The data will be available at `/data/` on aridhia workspace). This should be an absolute path.
`AICROWD_OUTPUTS_PATH` | Path to write the output to.
`AICROWD_ASSETS_DIR` | In case your notebook needs additional files (like model weights, etc.,), you can add them to a directory and specify the path to the directory here (please specify relative path). The contents of this directory will be sent to AIcrowd for evaluation.
`AICROWD_API_KEY` | In order to submit your code to AIcrowd, you need to provide your account's API key. This key is available at https://www.aicrowd.com/participants/me

- **Installing packages**. Please use the [Install packages 🗃](#Install-packages-🗃) section to install the packages
- **Training your models**. All the code within the [Training phase ⚙️](#Training-phase-⚙️) section will be skipped during evaluation. **Please make sure to save your model weights in the assets directory and load them in the predictions phase section** 

## AIcrowd Runtime Configuration 🧷

Define configuration parameters. Please include any files needed for the notebook to run under `ASSETS_DIR`. We will copy the contents of this directory to your final submission file 🙂

The dataset is available under `/data` on the workspace.

In [63]:
import os

# Please use the absolute for the location of the dataset.
# Or you can use relative path with `os.getcwd() + "test_data/test.csv"`
AICROWD_DATASET_PATH = os.getenv("DATASET_PATH", os.getcwd()+"/data/data.csv")
AICROWD_OUTPUTS_PATH = os.getenv("OUTPUTS_DIR", "")
AICROWD_ASSETS_DIR = os.getenv("ASSETS_DIR", "assets")

# Install packages 🗃

We are going to use many different libraries to demonstrate many idfferent techniques to convert text into numbers ( or more specifically vectors )

In [64]:
!pip install --upgrade spacy rich gensim tensorflow scikit-learn
!python -m spacy download en_core_web_sm # Downloaing the model for english language will contains many pretrained preprocessing pipelines 


Aborted!


# Define preprocessing code 💻

The code that is common between the training and the prediction sections should be defined here. During evaluation, we completely skip the training section. Please make sure to add any common logic between the training and prediction sections here.

In [65]:
# Importing Libraries
import pandas as pd
import numpy as np
np.warnings.filterwarnings('ignore', category=np.VisibleDeprecationWarning)
import random
from tqdm.notebook import tqdm

# Tensorflow 
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences

# Sklearn
from sklearn.tree import DecisionTreeClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import f1_score, accuracy_score


# Word2vec Implementation
import spacy
nlp = spacy.load('en_core_web_sm', exclude=['tagger', 'ner', 'attribute_ruler', 'lemmatizer'])

from gensim.models import Word2Vec
from gensim.models.phrases import Phrases, Phraser

# To make things more beautiful! 
from rich.console import Console
from rich.table import Table
from rich.segment import Segment
from rich import pretty
pretty.install()

# Seeding everything for getting same results 
random.seed(42)
np.random.seed(42)

# function to display YouTube videos
from IPython.display import YouTubeVideo

In [66]:
# Latest version of gensim
import gensim
gensim.__version__

'4.1.2'

In [67]:
# Defining the function for preprocessing test dataset which will run after submitting the notebook

def tokenize_sentence(sentences, num_words=1000, maxlen=256, show=False): 

  # Creating the tokenizer, the num_words represents the vocabulary and assigning OOV token ( out of vocaculary ) for unknown tokenn
  # Which can arise if we input a sentence containing a words that tokenizer don't have in his vocabulary

  tokenizer = Tokenizer(num_words=num_words, oov_token="<OOV>")


  tokenizer.fit_on_texts(sentences)
  
  # Getting the unique ID for each token
  word_index = tokenizer.word_index

  # Convert the senteces into vector
  sequences = tokenizer.texts_to_sequences(sentences)

  # Padding the vectors so that all vectors have the same length
  padded_sequences = pad_sequences(sequences, padding='post', truncating='pre', maxlen=maxlen)


  word_index = np.asarray(word_index)
  sequences = np.asarray(sequences)
  padded_sequences = np.asarray(padded_sequences)

  if show==True:
    console = Console()

    console.log("Word Index. A unique ID is assigned to each token.")
    console.log(word_index)
    console.log("---"*10)

    console.log("Sequences. senteces converted into vector.")
    console.log(np.array(sequences[0]))
    console.log("---"*10)

    console.log("Padded Sequences. Adding,( 0 in this case ) or removing elements to make all vectors in the samples same.")
    console.log(np.array(padded_sequences[0]))
    console.log("---"*10)



  return tokenizer, word_index, sequences, padded_sequences

# Training phase ⚙️

You can define your training code here. This sections will be skipped during evaluation.

## Downloading Dataset

Must be prety familar thing by now :) In case, here we are downloading the challange dataset using AIcrowd CLI 

In [68]:
%aicrowd login

Please login here: https://api.aicrowd.com/auth/jEBysoL_AZqhovB-oUp3Ji8Kqgw2do145DtI4nzwdQw
API Key valid
Saved API Key successfully!


In [69]:
# Downloading the Dataset
!mkdir data

# Donwloading programming language classification dataset for testing purposes
!mkdir programming-language-data


mkdir: cannot create directory ‘data’: File exists
data.csv: 100% 8.37k/8.37k [00:00<00:00, 364kB/s]
mkdir: cannot create directory ‘programming-language-data’: File exists
train.csv:   0% 0.00/7.71M [00:00<?, ?B/s]
test.csv:   0% 0.00/1.50M [00:00<?, ?B/s]

sample_submission.csv:   0% 0.00/121k [00:00<?, ?B/s]

sample_submission.csv: 100% 121k/121k [00:00<00:00, 368kB/s]

test.csv: 100% 1.50M/1.50M [00:00<00:00, 1.75MB/s]
train.csv: 100% 7.71M/7.71M [00:01<00:00, 6.17MB/s]


### Reading Dataset

Reading the necessary files to train, validation & submit our results! 

We are also using [Programming Language Challange](https://www.aicrowd.com/challenges/ai-blitz-xii/problems/programming-language-classification) dataset for testing purposes.

In [70]:
dataset = pd.read_csv("data/data.csv")
train_data = pd.read_csv("programming-language-data/train.csv")

dataset

id 
 text 
 feature 
 
 
 
 
 0 
 0 
 Incels can't even get a pleb thing called sex.... 
 [0, 1, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 1, ... 
 
 
 1 
 1 
 Seriously? I couldn't even remember the dude's... 
 [0, 1, 1, 0, 0, 1, 0, 0, 0, 1, 1, 1, 0, 0, 1, ... 
 
 
 2 
 2 
 Seeing [NAME] on Sunday and I'm so fucking stoked 
 [0, 1, 1, 0, 1, 1, 1, 1, 1, 0, 1, 0, 1, 0, 0, ... 
 
 
 3 
 3 
 Your not winning their hearts, your just tortu... 
 [1, 0, 0, 0, 0, 1, 1, 0, 0, 1, 1, 0, 0, 0, 1, ... 
 
 
 4 
 4 
 This sub needs more Poison memes. 
 [1, 1, 1, 0, 0, 0, 0, 1, 0, 1, 0, 1, 1, 0, 0, ... 
 
 
 5 
 5 
 It is part of the political game unfortunately. 
 [1, 0, 0, 0, 0, 1, 1, 1, 1, 0, 0, 0, 1, 0, 1, ... 
 
 
 6 
 6 
 That looks lovely, but what’s the mutant on th... 
 [0, 1, 1, 0, 0, 0, 1, 0, 1, 1, 1, 0, 0, 1, 0, ... 
 
 
 7 
 7 
 Who will rid me of these meddlesome Golden Kni... 
 [0, 0, 1, 1, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 1, ... 
 
 
 8 
 8 
 We were all duped? I’ve seen through her from ... 
 [0, 0, 1, 0, 1, 1, 0, 0, 1, 0, 1, 0, 0, 1, 0, ... 
 
 
 9 
 9 
 "Lol, hold my craft beer." 
 [0, 0, 1, 1, 0, 0, 1, 1, 0, 0, 0, 0, 1, 0, 0, ...

## Creating our Templete

So, with this `train_model` we are going to text the various differetn techniques and pare to see which works best!

In [71]:
def train_model(X, y):

  # Splitting the dataset into training and testing,  also by using stratify, we are making sure to use the same class balance between training and testing. 
  X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, stratify=y, random_state=42)

  # Creating and training sklearn's Decision Tree Classifier Model 
  clf = DecisionTreeClassifier(random_state=42)
  clf.fit(X_train, y_train)

  # Getting the predictions form unseen (testing dataset)
  predictions = clf.predict(X_test)

  # Calcuating the metrics 
  f1 = f1_score(y_test, predictions, average='weighted')
  accuracy = accuracy_score(y_test, predictions)

  # Creating the table
  console = Console()
  result_table = Table(show_header=False, header_style="bold magenta")

  result_table.add_row("F1 Score", str(f1))
  result_table.add_row("Accuracy Score", str(accuracy))

  # Showing the table
  console.print(result_table)

  return f1, accuracy

## Simple Tokenization 🪙

Here, all what we are doing is splitting the senteces into tokens/words, and then assigning a unique id to each token, and here we go, we converted the text into a vector. We are also using padding to make sure all vectors are of `maxlen` which is 256. 

In [72]:
def tokenize_sentence(sentences, num_words=10000, maxlen=256, show=False): 

  # Creating the tokenizer, the num_words represents the vocabulary and assigning OOV token ( out of vocaculary ) for unknown tokenn
  # Which can arise if we input a sentence containing a words that tokenizer don't have in his vocabulary

  tokenizer = Tokenizer(num_words=num_words, oov_token="<OOV>")


  tokenizer.fit_on_texts(sentences)
  
  # Getting the unique ID for each token
  word_index = tokenizer.word_index

  # Convert the senteces into vector
  sequences = tokenizer.texts_to_sequences(sentences)

  # Padding the vectors so that all vectors have the same length
  padded_sequences = pad_sequences(sequences, padding='post', truncating='pre', maxlen=maxlen)


  word_index = np.asarray(word_index)
  sequences = np.asarray(sequences)
  padded_sequences = np.asarray(padded_sequences)

  if show==True:
    console = Console()

    console.log("Word Index. A unique ID is assigned to each token.")
    console.log(word_index)
    console.log("---"*10)

    console.log("Sequences. senteces converted into vector.")
    console.log(np.array(sequences[0]))
    console.log("---"*10)

    console.log("Padded Sequences. Adding,( 0 in this case ) or removing elements to make all vectors in the samples same.")
    console.log(np.array(padded_sequences[0]))
    console.log("---"*10)



  return tokenizer, word_index, sequences, padded_sequences

In [73]:
# Sample Senteces
sample_sentences = dataset.iloc[0, 1].split(".")
sample_sentences

[
    "Incels can't even get a pleb thing called sex",
    ' Sex is for [NAME] apparently',
    ''
]

In [74]:
_, _, _, _ = tokenize_sentence(sample_sentences, num_words=50, maxlen=16, show=True)

[14:43:41] Word Index. A unique ID is assigned to each     <ipython-input-72-034b9db2f918>:28
           token.

           {'<OOV>': 1, 'sex': 2, 'incels': 3, "can't": 4, <ipython-input-72-034b9db2f918>:29
           'even': 5, 'get': 6, 'a': 7, 'pleb': 8,                                           
           'thing': 9, 'called': 10, 'is': 11, 'for': 12,                                    
           'name': 13, 'apparently': 14}

           ------------------------------                  <ipython-input-72-034b9db2f918>:30

           Sequences. senteces converted into vector.      <ipython-input-72-034b9db2f918>:32

           [ 3  4  5  6  7  8  9 10  2]                    <ipython-input-72-034b9db2f918>:33

           ------------------------------                  <ipython-input-72-034b9db2f918>:34

           Padded Sequences. Adding,( 0 in this case ) or  <ipython-input-72-034b9db2f918>:36
           removing elements to make all vectors in the                                      
           samples same.

           [ 3  4  5  6  7  8  9 10  2  0  0  0  0  0  0   <ipython-input-72-034b9db2f918>:37
           0]

           ------------------------------                  <ipython-input-72-034b9db2f918>:38

In [75]:
# Training the model using the vectors and the features

tokenizer, _, _, X = tokenize_sentence(train_data['code'].values)
y = train_data['language'].values

In [76]:
print("Sentence : ", train_data['code'][2])
print("Simple Tokenizer : ", X[2])

Sentence :  /*

     Explanation :- a user gives a String (it can be incomplete uppercase or

         partial uppercase) and then the program would convert it into a

         complete(all characters in lower case) lower case string. The

Simple Tokenizer :  [ 862    8  377 1465    8   33   90  179   49    1 1531  109 3361 1531
   24  247    3  467  821  442   90  295    8 1489  123  450   15  372
  156  372  156   33    3    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0

In [77]:
token_id_f1, token_id_accuracy = train_model(X, y)

┏━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━┓
┃ F1 Score       ┃ 0.45817492992728615 ┃
│ Accuracy Score │ 0.4591277668200745  │
└────────────────┴─────────────────────┘

Now, the advantages of this method is that it is very simple, but one of the major disadvantages for this is it doesn't contain the "meaning" of the text, and mny next will also not be able to solve this issue, unzip word2vec  

## Bag of Words 🎒

In Bag of Words, instead of what we did in simple tokenization, just assiging a unique ID to each token, bag of words, does things a little different.

I find bag of words harder to understand with a text, so i find [this](https://youtu.be/UFtXy0KRxVI) video really helpful for understand bag of words in a more visual way. Be sure to watch it. 

In [78]:
tokenizer, _, _, _ = tokenize_sentence(train_data['code'].values, num_words=256)
X = tokenizer.texts_to_matrix(train_data['code'].values)

In [79]:
print("Sentence : ", train_data['code'][0])
print("BOW : ", X[0])

Sentence :              var result = testObj1 | testObj2;

             // Assert

             Assert.AreEqual(expected, result.ToString());

         }

         [TestCase(1, 1, 1, 1, "1")]

         [TestCase(5, 3, 8, 4, "0000")]

BOW :  [0. 1. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0.
 0. 0. 0. 0. 1. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0

In [80]:
bow_f1, bow_accuracy = train_model(X, y)

┏━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━┓
┃ F1 Score       ┃ 0.674054615101746  ┃
│ Accuracy Score │ 0.6753232522463292 │
└────────────────┴────────────────────┘

Yee! both of the metrics did increased! Advantages of Bag of words is that it's again, really simple, but it doesn't keep the same order of words in sentence and doesn't keep the meaning of the sentence.  

## Count Vectorization 🔢

Count Vectorization is also very similar to Bag of Wards but instead of one hot, it also include the count of each token in a sentece. 

In [81]:
tokenizer, _, _, _ = tokenize_sentence(train_data['code'].values, num_words=256)
X = tokenizer.texts_to_matrix(train_data['code'].values, mode='count')

In [82]:
print("Sentence : ", train_data['code'][2])
print("CV : ", X[2])

Sentence :  /*

     Explanation :- a user gives a String (it can be incomplete uppercase or

         partial uppercase) and then the program would convert it into a

         complete(all characters in lower case) lower case string. The

CV :  [ 0. 15.  0.  2.  0.  0.  0.  0.  3.  0.  0.  0.  0.  0.  0.  1.  0.  0.
  0.  0.  0.  0.  0.  0.  1.  0.  0.  0.  0.  0.  0.  0.  0.  2.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  1.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  2.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  1.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  1.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  2.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  1.
  0.  0.  0.  0.  0.  0.

In [83]:
count_f1, count_accuracy = train_model(X, y)

┏━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━┓
┃ F1 Score       ┃ 0.6620297368099443 ┃
│ Accuracy Score │ 0.663488932719702  │
└────────────────┴────────────────────┘

## TF - IDF 📐

TF-IDF is **Term Frequency - Inverse Document Frequency**. So as we way in last section, about count frequency, that had a bit of flaw, for ex. tokens such a `is, are, the` are very common and will generally have bigger counts, but they don't ususally help for ex. classify whether the text is positive or negative. TF-IDF actually try to solve this issue. TF-IDF applies lower score to the common tokens and higher scores for more rarer tokens. 

In [84]:
tokenizer, _, _, _ = tokenize_sentence(train_data['code'].values, num_words=256)
X = tokenizer.texts_to_matrix(train_data['code'].values, mode='tfidf')

In [85]:
print("Sentence : ", train_data['code'][0])
print("TF-IDF : ", X[0])

Sentence :              var result = testObj1 | testObj2;

             // Assert

             Assert.AreEqual(expected, result.ToString());

         }

         [TestCase(1, 1, 1, 1, "1")]

         [TestCase(5, 3, 8, 4, "0000")]

TF-IDF :  [ 0.         31.60460419  4.23447758  0.          0.          0.
  0.          0.          0.          0.          0.          0.
  0.          0.          0.          0.          0.          0.
  0.          2.57234506  0.          0.          0.          0.
  0.          0.          0.          0.          2.88231493  2.92883682
  0.          0.          0.          0.          0.          0.
  0.          0.          0.          0.          0.          0.
  0.          0.          0.          0.          0.          0.
  0.          0.          0.          0.          0.          0.
  0.          0.          0.          0.          0.          0.
  0.          0.          5.82824057  0.          0.          0.
  0.          0.          0.     

In [ ]:
tfidf_f1, tfidf_accuracy = train_model(X, y)

┏━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━┓
┃ F1 Score       ┃ 0.6625065598878417 ┃
│ Accuracy Score │ 0.6640368178829718 │
└────────────────┴────────────────────┘

# Prediction phase 🔎

Generating the features in test dataset. 

In [ ]:
test_dataset = pd.read_csv(AICROWD_DATASET_PATH)
test_dataset

id 
 text 
 feature 
 
 
 
 
 0 
 0 
 Incels can't even get a pleb thing called sex.... 
 [0, 1, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 1, ... 
 
 
 1 
 1 
 Seriously? I couldn't even remember the dude's... 
 [0, 1, 1, 0, 0, 1, 0, 0, 0, 1, 1, 1, 0, 0, 1, ... 
 
 
 2 
 2 
 Seeing [NAME] on Sunday and I'm so fucking stoked 
 [0, 1, 1, 0, 1, 1, 1, 1, 1, 0, 1, 0, 1, 0, 0, ... 
 
 
 3 
 3 
 Your not winning their hearts, your just tortu... 
 [1, 0, 0, 0, 0, 1, 1, 0, 0, 1, 1, 0, 0, 0, 1, ... 
 
 
 4 
 4 
 This sub needs more Poison memes. 
 [1, 1, 1, 0, 0, 0, 0, 1, 0, 1, 0, 1, 1, 0, 0, ... 
 
 
 5 
 5 
 It is part of the political game unfortunately. 
 [1, 0, 0, 0, 0, 1, 1, 1, 1, 0, 0, 0, 1, 0, 1, ... 
 
 
 6 
 6 
 That looks lovely, but what’s the mutant on th... 
 [0, 1, 1, 0, 0, 0, 1, 0, 1, 1, 1, 0, 0, 1, 0, ... 
 
 
 7 
 7 
 Who will rid me of these meddlesome Golden Kni... 
 [0, 0, 1, 1, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 1, ... 
 
 
 8 
 8 
 We were all duped? I’ve seen through her from ... 
 [0, 0, 1, 0, 1, 1, 0, 0, 1, 0, 1, 0, 0, 1, 0, ... 
 
 
 9 
 9 
 "Lol, hold my craft beer." 
 [0, 0, 1, 1, 0, 0, 1, 1, 0, 0, 0, 0, 1, 0, 0, ...

In [ ]:
# So, let's do a simple tokenization and generate the features!

tokenizer, _, _, X = tokenize_sentence(test_dataset['text'].values,num_words=256)
X = tokenizer.texts_to_matrix(test_dataset['text'].values, mode='freq')

for index, row in tqdm(test_dataset.iterrows()):
  test_dataset.iloc[index, 2] = str(X[index].tolist())

test_dataset

0it [00:00, ?it/s]

id 
 text 
 feature 
 
 
 
 
 0 
 0 
 Incels can't even get a pleb thing called sex.... 
 [0.0, 0.0, 0.0, 0.07142857142857142, 0.0714285... 
 
 
 1 
 1 
 Seriously? I couldn't even remember the dude's... 
 [0.0, 0.0, 0.13333333333333333, 0.066666666666... 
 
 
 2 
 2 
 Seeing [NAME] on Sunday and I'm so fucking stoked 
 [0.0, 0.0, 0.0, 0.0, 0.0, 0.1111111111111111, ... 
 
 
 3 
 3 
 Your not winning their hearts, your just tortu... 
 [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ... 
 
 
 4 
 4 
 This sub needs more Poison memes. 
 [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ... 
 
 
 5 
 5 
 It is part of the political game unfortunately. 
 [0.0, 0.0, 0.125, 0.0, 0.125, 0.0, 0.0, 0.0, 0... 
 
 
 6 
 6 
 That looks lovely, but what’s the mutant on th... 
 [0.0, 0.0, 0.2, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ... 
 
 
 7 
 7 
 Who will rid me of these meddlesome Golden Kni... 
 [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ... 
 
 
 8 
 8 
 We were all duped? I’ve seen through her from ... 
 [0.0, 0.0, 0.0, 0.05555555555555555, 0.0555555... 
 
 
 9 
 9 
 "Lol, hold my craft beer." 
 [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...

In [ ]:
# Saving the sample submission
test_dataset.to_csv(os.path.join(AICROWD_OUTPUTS_PATH,'submission.csv'), index=False)

# Submit to AIcrowd 🚀

**Note : Please save the notebook before submitting it (Ctrl + S)**

In [ ]:
%aicrowd notebook submit --assets-dir $AICROWD_ASSETS_DIR --challenge nlp-feature-engineering-2 --no-verify

Congratulations 🎉 you did it, but there still a lot of improvement that can be made, this is feature engineering challange after all, means that we have to fit as much information as we can about the text in `256` numbers. We only covered converting texts into vector, but there are so many things you can try more, for ex. unsupervised classification, idk, maybe it can help :)

And btw -

> Don't be shy to ask question related to any errors you are getting or doubts in any part of this notebook in [discussion forum](https://www.aicrowd.com/challenges/ai-blitz-xii/problems/nlp-feature-engineering-2/discussion) or in [AIcrowd Discord sever](https://discord.gg/T6uZSWBMSZ), AIcrew will be happy to help you :)

Also, wanna give us your valuable feedback for next blitz or wanna work with us creating blitz challanges ? Let us know! 